In [1]:
import keras.backend as K
import tensorflow as tf
from keras.layers import Input
from keras.activations import softplus
from keras.models import Model
from keras.optimizers import Adam
import numpy as np
import matplotlib.pyplot as plt
import argparse
import keras.backend as K
import tensorflow as tf
import numpy as np
from keras.layers import Input, Reshape, Flatten,Dense,BatchNormalization,PReLU
from keras.layers import Activation, Add,Lambda,AveragePooling2D,LeakyReLU,GlobalAvgPool2D
from keras.layers.convolutional import UpSampling2D, Conv2D
from keras.models import Model
from keras.initializers import RandomNormal,glorot_uniform
import pandas as pd
from keras.preprocessing.image import load_img
from tqdm import tqdm_notebook
conv_init = RandomNormal(0, 0.02)

Using TensorFlow backend.


In [2]:
def Resblock_generator(layer_input,channels):
    # h1 = BatchNormalization(momentum=0.9)(layer_input)
    h1 = UpSampling2D(size=2)(layer_input)
    h1 = Conv2D(channels,3,strides=1,padding="same",kernel_initializer=conv_init)(h1)
    # h1 = SubpixelConv2D(h1)(h1)
    h1 = BatchNormalization(momentum=0.9)(h1)
    # h1 = Activation("relu")(h1)

    h2 = UpSampling2D(size=2)(layer_input)
    h2 = Conv2D(channels,1,strides=1,padding="valid",kernel_initializer=conv_init)(h2)
    # h2 = SubpixelConv2D(layer_input)(h2)
    # h2 = Activation("relu")(h2)

    return Add()([h2,h1])

def Generator(z_dim,base=64):
    input = Input(shape=(z_dim,))
    h = Dense(128*8*8)(input)
    h = Reshape((8,8,128))(h)
    # h = Resblock_generator(h,base*4)
    # h = Resblock_generator(h,base*4)
    h = Resblock_generator(h,base*4)
    h = Resblock_generator(h,base*2)
    h = Resblock_generator(h,base)
    h = BatchNormalization(momentum=0.9)(h)
    h = PReLU()(h)
    h = Conv2D(3,3,strides=1,padding='same')(h)
    output = Activation('tanh')(h)
    model = Model(inputs=input,outputs=output)
    model.summary()
    return model

def Resblock_discriminator(layer_input,channels):
    h1 = Conv2D(channels,3,strides=1,padding='same',kernel_initializer=conv_init)(layer_input)
    h1 = LeakyReLU(alpha=0.2)(h1)
    h1 = Conv2D(channels,3,strides=1,padding='same',kernel_initializer=conv_init)(h1)
    h1 = AveragePooling2D(pool_size=(2, 2))(h1)

    h2 = Conv2D(channels,1,strides=1,padding="valid",kernel_initializer=conv_init)(layer_input)
    h2 = LeakyReLU(alpha=0.2)(h2)
    h2 = AveragePooling2D(pool_size=(2, 2))(h2)

    return Add()([h2,h1])

def Discriminator(input_shape,base=64):
    input = Input(shape=input_shape)
    h = Resblock_discriminator(input,base)
    h = Resblock_discriminator(h,base*2)
    h = Resblock_discriminator(h,base*4)
    # h = Resblock_discriminator(h,base*4)
    h = Resblock_discriminator(h,base*8)
    h = LeakyReLU(alpha=0.2)(h)
    # h = GlobalAvgPool2D()(h)
    h = Flatten()(h)
    # h = Dense(1024)(h)
    output = Dense(1)(h)
    model = Model(inputs=input,outputs=output)
    model.summary()
    return model

In [3]:
epochs = 50
save_interval = 1
model_interval = 1
batch_size = 32
_lambda = 0.5

z_dim = 100
img_shape = (64, 64, 3)
image_size = 64
channels = 3
lr_D = 2e-4
lr_G = 2e-4
b1 = 0.5
b2 = 0.99

gen = Generator(z_dim)
dis = Discriminator(img_shape)

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 100)          0                                            
__________________________________________________________________________________________________
dense_1 (Dense)                 (None, 8192)         827392      input_1[0][0]                    
__________________________________________________________________________________________________
reshape_1 (Reshape)             (None, 8, 8, 128)    0           dense_1[0][0]                    
__________________________________________________________________________________________________
up_sampling2d_1 (UpSampling2D)  (None, 16, 16, 128)  0           reshape_1[0][0]                  
__________________________________________________________________________________________________
up_samplin

In [4]:
# -------------------------
# compute grandient penalty
# -------------------------

dis_real = Input(shape=(image_size, image_size, channels))
noisev = Input(shape=(z_dim,))
dis_fake = gen(noisev)
valid = dis(dis_fake)

delta_input = K.placeholder(shape=(None, image_size, image_size, channels))
# alpha = K.random_uniform(
#     shape=[batch_size, 1, 1, 1],
#     minval=0.,
#     maxval=1.
# )

dis_mixed = Input(shape=(image_size, image_size, channels),
                  tensor=dis_real + delta_input)

loss_real = K.sum(K.softplus(-dis(dis_real))) / batch_size
loss_fake = K.sum(K.softplus(valid)) / batch_size

# dis_mixed_real = alpha * dis_real + ((1 - alpha) * dis_mixed)

grad_mixed = K.gradients(dis(dis_mixed), [dis_mixed])[0]
norm = K.sqrt(K.sum(K.square(grad_mixed), axis=[1, 2, 3]))
grad_penalty = K.mean(K.square(norm - 1))
loss_dis = loss_fake + loss_real + _lambda * grad_penalty

In [5]:
# ---------------------
# loss for discriminator
# ---------------------

training_updates = Adam(lr=lr_D, beta_1=b1,beta_2=b2).get_updates(
    dis.trainable_weights, [], loss_dis)
dis_train = K.function([dis_real, noisev, delta_input],
                       [loss_real, loss_fake],
                       training_updates)

In [6]:
# -----------------
# loss for generator
# -----------------

loss_gen = K.sum(K.softplus(-valid)) / batch_size

training_updates = Adam(lr=lr_G, beta_1=b1,beta_2=b2).get_updates(
    gen.trainable_weights, [], loss_gen)
gen_train = K.function([noisev],
                       [loss_gen],
                       training_updates)


In [7]:

tags = pd.read_csv('./extra_data/extra_data/convert_tags.csv')
X_train = np.array([(np.array(load_img("./extra_data/extra_data/images/{}.jpg".format(ids))) / 127.5 - 1) for ids in tqdm_notebook(tags.idx)])


A Jupyter Widget

In [8]:
fixed_noise = np.random.normal(size=(16, z_dim))
batch = X_train.shape[0] // batch_size
gen_logit = np.ones((batch_size,image_size,image_size,channels))
for epoch in range(epochs):
    print("Epoch is", epoch)
    for index in range(batch):
        idx = np.random.randint(0, X_train.shape[0], batch_size)
        image_batch = X_train[idx]
        image_batch = np.float32(image_batch)
        noise = np.random.normal(size=(batch_size, z_dim))
        delta = 0.5 * image_batch.std() * np.random.random(size=image_batch.shape)
        delta *= np.random.uniform(size=(batch_size, 1, 1, 1))
        errD_real, errD_fake = dis_train([image_batch, noise, delta])
        errD = errD_real - errD_fake

        errG, = gen_train([noise])
        print('%d/%d  Loss_D: %f Loss_G: %f Loss_D_real: %f Loss_D_fake %f'
              % (index, batch, errD, errG, errD_real, errD_fake))

        if (epoch % save_interval == 0 and index == 0) or index%300 == 0:
            gen_imgs = gen.predict(fixed_noise)
            r, c = 4,4
            # Rescale images 0 - 1
            gen_imgs = 0.5 * gen_imgs + 0.5
            fig, axs = plt.subplots(r, c)
            cnt = 0
            for i in range(r):
                for j in range(c):
                    axs[i, j].imshow(gen_imgs[cnt])
                    axs[i, j].axis('off')
                    cnt += 1
            fig.savefig("DRAGAN_result/%d_%d.png" % (epoch,index))
            plt.close()
            if epoch % model_interval == 0 and index == 0:
                 gen.save("DRAGAN_model/model-{}-epoch.h5".format(epoch))

Epoch is 0
0/1148  Loss_D: -0.002113 Loss_G: 0.692280 Loss_D_real: 0.691258 Loss_D_fake 0.693372
1/1148  Loss_D: -0.030468 Loss_G: 0.692031 Loss_D_real: 0.664114 Loss_D_fake 0.694583
2/1148  Loss_D: -0.128715 Loss_G: 0.695117 Loss_D_real: 0.569866 Loss_D_fake 0.698581
3/1148  Loss_D: -0.398384 Loss_G: 0.643905 Loss_D_real: 0.327255 Loss_D_fake 0.725639
4/1148  Loss_D: -0.891343 Loss_G: 0.652508 Loss_D_real: 0.027978 Loss_D_fake 0.919320
5/1148  Loss_D: -1.072846 Loss_G: 0.742694 Loss_D_real: 0.051409 Loss_D_fake 1.124255
6/1148  Loss_D: -0.322660 Loss_G: 0.762411 Loss_D_real: 0.360668 Loss_D_fake 0.683328
7/1148  Loss_D: -0.420836 Loss_G: 0.730110 Loss_D_real: 0.285443 Loss_D_fake 0.706279
8/1148  Loss_D: -0.953077 Loss_G: 0.958257 Loss_D_real: 0.132586 Loss_D_fake 1.085663
9/1148  Loss_D: -0.003153 Loss_G: 0.933925 Loss_D_real: 0.558606 Loss_D_fake 0.561759
10/1148  Loss_D: -0.280208 Loss_G: 1.047528 Loss_D_real: 0.442603 Loss_D_fake 0.722811
11/1148  Loss_D: 0.062131 Loss_G: 1.245125

95/1148  Loss_D: 0.386010 Loss_G: 0.764628 Loss_D_real: 0.787144 Loss_D_fake 0.401134
96/1148  Loss_D: -0.421143 Loss_G: 1.317893 Loss_D_real: 0.319114 Loss_D_fake 0.740258
97/1148  Loss_D: 0.155440 Loss_G: 1.194722 Loss_D_real: 0.552105 Loss_D_fake 0.396665
98/1148  Loss_D: -0.095969 Loss_G: 1.000933 Loss_D_real: 0.485839 Loss_D_fake 0.581809
99/1148  Loss_D: -0.312646 Loss_G: 1.412742 Loss_D_real: 0.447183 Loss_D_fake 0.759829
100/1148  Loss_D: -0.205081 Loss_G: 1.106362 Loss_D_real: 0.754059 Loss_D_fake 0.959139
101/1148  Loss_D: -0.067371 Loss_G: 1.199867 Loss_D_real: 0.853905 Loss_D_fake 0.921277
102/1148  Loss_D: -0.131807 Loss_G: 1.105782 Loss_D_real: 0.520447 Loss_D_fake 0.652254
103/1148  Loss_D: -0.611748 Loss_G: 2.736976 Loss_D_real: 0.436545 Loss_D_fake 1.048292
104/1148  Loss_D: 1.992015 Loss_G: 0.331314 Loss_D_real: 2.080788 Loss_D_fake 0.088773
105/1148  Loss_D: -1.257006 Loss_G: 0.746889 Loss_D_real: 0.177756 Loss_D_fake 1.434762
106/1148  Loss_D: -0.226990 Loss_G: 1.05

189/1148  Loss_D: 0.018626 Loss_G: 1.674444 Loss_D_real: 0.612275 Loss_D_fake 0.593650
190/1148  Loss_D: 0.623551 Loss_G: 0.615545 Loss_D_real: 1.039906 Loss_D_fake 0.416355
191/1148  Loss_D: -0.576363 Loss_G: 2.837023 Loss_D_real: 0.397560 Loss_D_fake 0.973923
192/1148  Loss_D: 0.895683 Loss_G: 0.967293 Loss_D_real: 1.191131 Loss_D_fake 0.295448
193/1148  Loss_D: -0.011538 Loss_G: 0.849818 Loss_D_real: 0.635347 Loss_D_fake 0.646885
194/1148  Loss_D: -0.569849 Loss_G: 1.635533 Loss_D_real: 0.382954 Loss_D_fake 0.952803
195/1148  Loss_D: 0.081598 Loss_G: 1.705669 Loss_D_real: 0.545443 Loss_D_fake 0.463845
196/1148  Loss_D: 0.227783 Loss_G: 0.665475 Loss_D_real: 0.745365 Loss_D_fake 0.517582
197/1148  Loss_D: -0.755642 Loss_G: 0.882607 Loss_D_real: 0.309471 Loss_D_fake 1.065113
198/1148  Loss_D: -0.272290 Loss_G: 0.884689 Loss_D_real: 0.489602 Loss_D_fake 0.761892
199/1148  Loss_D: -0.042842 Loss_G: 1.016445 Loss_D_real: 0.512882 Loss_D_fake 0.555724
200/1148  Loss_D: -0.008768 Loss_G: 1

283/1148  Loss_D: 0.225298 Loss_G: 1.435174 Loss_D_real: 0.503055 Loss_D_fake 0.277757
284/1148  Loss_D: -0.405474 Loss_G: 2.825014 Loss_D_real: 0.201757 Loss_D_fake 0.607231
285/1148  Loss_D: 1.427798 Loss_G: 1.014270 Loss_D_real: 1.537028 Loss_D_fake 0.109230
286/1148  Loss_D: -0.407196 Loss_G: 1.010464 Loss_D_real: 0.305959 Loss_D_fake 0.713155
287/1148  Loss_D: -0.318783 Loss_G: 1.436147 Loss_D_real: 0.339346 Loss_D_fake 0.658129
288/1148  Loss_D: 0.271100 Loss_G: 1.045931 Loss_D_real: 0.656147 Loss_D_fake 0.385047
289/1148  Loss_D: -0.241570 Loss_G: 1.307885 Loss_D_real: 0.437498 Loss_D_fake 0.679068
290/1148  Loss_D: 0.109864 Loss_G: 1.354989 Loss_D_real: 0.482781 Loss_D_fake 0.372917
291/1148  Loss_D: 0.042044 Loss_G: 1.282099 Loss_D_real: 0.439709 Loss_D_fake 0.397666
292/1148  Loss_D: -0.321713 Loss_G: 2.247094 Loss_D_real: 0.268406 Loss_D_fake 0.590119
293/1148  Loss_D: 0.818118 Loss_G: 0.292410 Loss_D_real: 0.991199 Loss_D_fake 0.173081
294/1148  Loss_D: -2.545450 Loss_G: 2.

377/1148  Loss_D: -0.217352 Loss_G: 1.104143 Loss_D_real: 0.604778 Loss_D_fake 0.822129
378/1148  Loss_D: 0.374371 Loss_G: 0.946039 Loss_D_real: 0.858908 Loss_D_fake 0.484537
379/1148  Loss_D: 0.114648 Loss_G: 0.617696 Loss_D_real: 0.641590 Loss_D_fake 0.526943
380/1148  Loss_D: -0.646814 Loss_G: 1.439610 Loss_D_real: 0.363015 Loss_D_fake 1.009829
381/1148  Loss_D: 0.685712 Loss_G: 1.272490 Loss_D_real: 0.977143 Loss_D_fake 0.291431
382/1148  Loss_D: 0.331078 Loss_G: 0.832386 Loss_D_real: 0.706036 Loss_D_fake 0.374958
383/1148  Loss_D: -0.419006 Loss_G: 0.876714 Loss_D_real: 0.346041 Loss_D_fake 0.765047
384/1148  Loss_D: -0.510606 Loss_G: 1.266960 Loss_D_real: 0.471143 Loss_D_fake 0.981749
385/1148  Loss_D: 0.304111 Loss_G: 1.188035 Loss_D_real: 0.820324 Loss_D_fake 0.516214
386/1148  Loss_D: 0.501695 Loss_G: 0.814212 Loss_D_real: 1.003333 Loss_D_fake 0.501638
387/1148  Loss_D: -0.005624 Loss_G: 0.724902 Loss_D_real: 0.634061 Loss_D_fake 0.639684
388/1148  Loss_D: -0.371533 Loss_G: 1.

...

709/1148  Loss_D: -0.009512 Loss_G: 2.985195 Loss_D_real: 0.087690 Loss_D_fake 0.097202
710/1148  Loss_D: 0.019561 Loss_G: 2.910559 Loss_D_real: 0.093082 Loss_D_fake 0.073521
711/1148  Loss_D: 0.005994 Loss_G: 2.903752 Loss_D_real: 0.101840 Loss_D_fake 0.095845
712/1148  Loss_D: 0.021679 Loss_G: 2.757048 Loss_D_real: 0.099700 Loss_D_fake 0.078021
713/1148  Loss_D: -0.000781 Loss_G: 2.766960 Loss_D_real: 0.101265 Loss_D_fake 0.102047
714/1148  Loss_D: -0.051952 Loss_G: 3.290785 Loss_D_real: 0.088297 Loss_D_fake 0.140249
715/1148  Loss_D: 0.069236 Loss_G: 2.806534 Loss_D_real: 0.128360 Loss_D_fake 0.059124
716/1148  Loss_D: -0.024579 Loss_G: 2.935868 Loss_D_real: 0.083214 Loss_D_fake 0.107793
717/1148  Loss_D: 0.035630 Loss_G: 2.750652 Loss_D_real: 0.113691 Loss_D_fake 0.078061
718/1148  Loss_D: -0.028756 Loss_G: 3.004298 Loss_D_real: 0.082230 Loss_D_fake 0.110986
719/1148  Loss_D: 0.033859 Loss_G: 2.651109 Loss_D_real: 0.126148 Loss_D_fake 0.092289
720/1148  Loss_D: -0.027909 Loss_G: 3.

803/1148  Loss_D: -0.045947 Loss_G: 3.708726 Loss_D_real: 0.059052 Loss_D_fake 0.104999
804/1148  Loss_D: 0.154396 Loss_G: 2.058932 Loss_D_real: 0.209947 Loss_D_fake 0.055551
805/1148  Loss_D: -0.112619 Loss_G: 3.500273 Loss_D_real: 0.085904 Loss_D_fake 0.198524
806/1148  Loss_D: 0.142152 Loss_G: 1.922423 Loss_D_real: 0.211749 Loss_D_fake 0.069596
807/1148  Loss_D: -0.190542 Loss_G: 3.972712 Loss_D_real: 0.054279 Loss_D_fake 0.244821
808/1148  Loss_D: 0.174203 Loss_G: 2.647298 Loss_D_real: 0.204376 Loss_D_fake 0.030174
809/1148  Loss_D: -0.035536 Loss_G: 2.705732 Loss_D_real: 0.105648 Loss_D_fake 0.141184
810/1148  Loss_D: 0.010052 Loss_G: 2.887233 Loss_D_real: 0.113639 Loss_D_fake 0.103587
811/1148  Loss_D: 0.005509 Loss_G: 3.229598 Loss_D_real: 0.137596 Loss_D_fake 0.132087
812/1148  Loss_D: 0.033520 Loss_G: 2.947022 Loss_D_real: 0.107501 Loss_D_fake 0.073981
813/1148  Loss_D: 0.101210 Loss_G: 1.954812 Loss_D_real: 0.198763 Loss_D_fake 0.097553
814/1148  Loss_D: -0.197847 Loss_G: 4.3

897/1148  Loss_D: -0.113771 Loss_G: 4.065229 Loss_D_real: 0.076473 Loss_D_fake 0.190244
898/1148  Loss_D: 0.225690 Loss_G: 2.013768 Loss_D_real: 0.249732 Loss_D_fake 0.024042
899/1148  Loss_D: -0.248858 Loss_G: 3.801400 Loss_D_real: 0.051378 Loss_D_fake 0.300236
900/1148  Loss_D: 0.187265 Loss_G: 2.768750 Loss_D_real: 0.233124 Loss_D_fake 0.045858
901/1148  Loss_D: -0.053155 Loss_G: 2.982977 Loss_D_real: 0.079848 Loss_D_fake 0.133004
902/1148  Loss_D: 0.005401 Loss_G: 3.087638 Loss_D_real: 0.083466 Loss_D_fake 0.078064
903/1148  Loss_D: 0.011015 Loss_G: 2.915627 Loss_D_real: 0.112550 Loss_D_fake 0.101535
904/1148  Loss_D: 0.021130 Loss_G: 2.820465 Loss_D_real: 0.110660 Loss_D_fake 0.089530
905/1148  Loss_D: -0.025498 Loss_G: 2.973662 Loss_D_real: 0.090865 Loss_D_fake 0.116362
906/1148  Loss_D: 0.069553 Loss_G: 2.290525 Loss_D_real: 0.162299 Loss_D_fake 0.092745
907/1148  Loss_D: -0.095860 Loss_G: 3.456110 Loss_D_real: 0.076480 Loss_D_fake 0.172340
908/1148  Loss_D: 0.161758 Loss_G: 2.1

991/1148  Loss_D: 0.043248 Loss_G: 2.836145 Loss_D_real: 0.124613 Loss_D_fake 0.081365
992/1148  Loss_D: -0.037431 Loss_G: 3.119578 Loss_D_real: 0.085419 Loss_D_fake 0.122849
993/1148  Loss_D: 0.064851 Loss_G: 2.751249 Loss_D_real: 0.126383 Loss_D_fake 0.061533
994/1148  Loss_D: 0.000900 Loss_G: 2.659134 Loss_D_real: 0.099576 Loss_D_fake 0.098675
995/1148  Loss_D: -0.055037 Loss_G: 3.504020 Loss_D_real: 0.063803 Loss_D_fake 0.118840
996/1148  Loss_D: 0.061152 Loss_G: 3.014524 Loss_D_real: 0.129955 Loss_D_fake 0.068803
997/1148  Loss_D: 0.068402 Loss_G: 2.291457 Loss_D_real: 0.144207 Loss_D_fake 0.075805
998/1148  Loss_D: -0.038455 Loss_G: 3.068028 Loss_D_real: 0.103005 Loss_D_fake 0.141459
999/1148  Loss_D: 0.014965 Loss_G: 2.974500 Loss_D_real: 0.108501 Loss_D_fake 0.093536
1000/1148  Loss_D: 0.028352 Loss_G: 2.680783 Loss_D_real: 0.129319 Loss_D_fake 0.100967
1001/1148  Loss_D: -0.026469 Loss_G: 3.012296 Loss_D_real: 0.085508 Loss_D_fake 0.111977
1002/1148  Loss_D: 0.052637 Loss_G: 2

1084/1148  Loss_D: 0.003087 Loss_G: 2.621927 Loss_D_real: 0.112135 Loss_D_fake 0.109047
1085/1148  Loss_D: -0.065247 Loss_G: 3.523517 Loss_D_real: 0.076177 Loss_D_fake 0.141424
1086/1148  Loss_D: 0.136898 Loss_G: 2.339677 Loss_D_real: 0.186192 Loss_D_fake 0.049294
1087/1148  Loss_D: -0.098725 Loss_G: 3.317992 Loss_D_real: 0.054744 Loss_D_fake 0.153468
1088/1148  Loss_D: 0.056523 Loss_G: 2.962768 Loss_D_real: 0.122588 Loss_D_fake 0.066065
1089/1148  Loss_D: 0.041974 Loss_G: 2.233341 Loss_D_real: 0.129911 Loss_D_fake 0.087937
1090/1148  Loss_D: -0.111237 Loss_G: 3.510172 Loss_D_real: 0.080370 Loss_D_fake 0.191607
1091/1148  Loss_D: 0.086157 Loss_G: 2.851816 Loss_D_real: 0.131094 Loss_D_fake 0.044938
1092/1148  Loss_D: -0.008603 Loss_G: 2.733162 Loss_D_real: 0.099701 Loss_D_fake 0.108304
1093/1148  Loss_D: 0.031757 Loss_G: 2.559997 Loss_D_real: 0.144450 Loss_D_fake 0.112693
1094/1148  Loss_D: -0.060674 Loss_G: 3.644481 Loss_D_real: 0.086464 Loss_D_fake 0.147137
1095/1148  Loss_D: 0.077410